# 第15週 中文社群網路分析

In [1]:
! pip install pandas
! pip install numpy
! pip install pyvis
! pip install networkx
! pip install IPython

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 756.0/756.0 kB 5.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 10.6 MB/s eta 0:00:00


In [2]:
import pandas as pd
import numpy as np
import pyvis
import networkx as nx
import IPython

In [4]:
import os

from google.colab import drive
drive.mount('/content/drive')

os.chdir('/content/drive/MyDrive/社媒/project(final)') #切換該目錄
os.listdir() #確認目錄內容

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


['data', 'dict', 'font', 'sentiment analysis.ipynb', 'week15_zh.ipynb']

In [5]:
raw_data = pd.read_csv('./data/depression.csv')
raw_data = raw_data[raw_data.artComment != '[]']
raw_data = raw_data.sample(round(raw_data.shape[0]/4), random_state=2024)
print(raw_data.shape)
raw_data.head()

(1276, 11)


system_id                                             artUrl  \
4347       4348  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...   
6044       6045  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...   
1658       1659  https://www.ptt.cc/bbs/prozac/M.1663197814.A.8...   
7082       7083  https://www.ptt.cc/bbs/prozac/M.1710497869.A.0...   
6130       6131  https://www.ptt.cc/bbs/prozac/M.1703305070.A.9...   

                      artTitle              artDate     artPoster artCatagory  \
4347                      [陰天]  2023-06-18 18:48:24  superfreeman      prozac   
6044              [陰天]我好累又好爛（雷  2023-12-14 13:05:31    cien881021      prozac   
1658             [閒聊]失眠(七十六)幻覺  2022-09-15 07:23:32    littlewren      prozac   
7082  [閒聊]今天走45min32sec想跟忍者大師說  2024-03-15 18:17:45        kazusn      prozac   
6130                    [閒聊]記事  2023-12-23 12:17:48       hesione      prozac   

                                             artContent  \
4347  今天又做了一些調整，把重要科目移到上午和晚上，投報率較低的移到下午，沒想到有明顯感受到差異，...   
6044  昨天在圓山公園哭了一個小時\n還想著乾脆人間蒸發算了\n\n明明升上正職，論文也終於完成要畢...   
1658  偶爾會有睡前幻覺、醒前幻覺的經驗(\n#1VAHqwpm\n)，\n\n通常睡前的比較多中性...   
7082  其實我跟我哥並不好 他大我八歲 小時候常常打我 是打的很兇的那種\n\n我原諒他差不多是在四...   
6130  一放假就生病\n@&#*^…\n來勢洶洶什麼藥都壓不下去\n一直燒\n脖子背超級痠痛\n看來...   

                                             artComment            e_ip  \
4347  [{"cmtStatus": "→", "cmtPoster": "qaz996659", ...  114.27.206.149   
6044  [{"cmtStatus": "推", "cmtPoster": "timer000", "...  223.137.57.231   
1658  [{"cmtStatus": "推", "cmtPoster": "qien", "cmtC...   223.140.62.26   
7082  [{"cmtStatus": "推", "cmtPoster": "isaki1987", ...  114.26.205.222   
6130  [{"cmtStatus": "推", "cmtPoster": "isaki1987", ...  184.153.120.32   

             insertedDate dataSource  
4347  2023-06-19 02:07:30        ptt  
6044  2023-12-15 02:19:21        ptt  
1658  2022-09-16 02:00:40        ptt  
7082  2024-03-16 02:24:04        ptt  
6130  2023-12-24 02:12:25        ptt

# 發文者與留言者關係

取得留言者跟狀態（推)

In [6]:
# parse comment
# 處理某篇文章的所有留言（取出留言者與狀態）
def getComtInfo(com):
  cmters,cmt_statuss = [],[]
  com = eval(com)
  for i in com:
    # print(i)
    cmters.append(i['cmtPoster'])
    cmt_statuss.append(i['cmtStatus'])
  return pd.Series([cmters, cmt_statuss])

raw_data[['artComter','artStatus']] = raw_data['artComment'].apply(lambda r: getComtInfo(r))
raw_data.head()

system_id                                             artUrl  \
4347       4348  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...   
6044       6045  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...   
1658       1659  https://www.ptt.cc/bbs/prozac/M.1663197814.A.8...   
7082       7083  https://www.ptt.cc/bbs/prozac/M.1710497869.A.0...   
6130       6131  https://www.ptt.cc/bbs/prozac/M.1703305070.A.9...   

                      artTitle              artDate     artPoster artCatagory  \
4347                      [陰天]  2023-06-18 18:48:24  superfreeman      prozac   
6044              [陰天]我好累又好爛（雷  2023-12-14 13:05:31    cien881021      prozac   
1658             [閒聊]失眠(七十六)幻覺  2022-09-15 07:23:32    littlewren      prozac   
7082  [閒聊]今天走45min32sec想跟忍者大師說  2024-03-15 18:17:45        kazusn      prozac   
6130                    [閒聊]記事  2023-12-23 12:17:48       hesione      prozac   

                                             artContent  \
4347  今天又做了一些調整，把重要科目移到上午和晚上，投報率較低的移到下午，沒想到有明顯感受到差異，...   
6044  昨天在圓山公園哭了一個小時\n還想著乾脆人間蒸發算了\n\n明明升上正職，論文也終於完成要畢...   
1658  偶爾會有睡前幻覺、醒前幻覺的經驗(\n#1VAHqwpm\n)，\n\n通常睡前的比較多中性...   
7082  其實我跟我哥並不好 他大我八歲 小時候常常打我 是打的很兇的那種\n\n我原諒他差不多是在四...   
6130  一放假就生病\n@&#*^…\n來勢洶洶什麼藥都壓不下去\n一直燒\n脖子背超級痠痛\n看來...   

                                             artComment            e_ip  \
4347  [{"cmtStatus": "→", "cmtPoster": "qaz996659", ...  114.27.206.149   
6044  [{"cmtStatus": "推", "cmtPoster": "timer000", "...  223.137.57.231   
1658  [{"cmtStatus": "推", "cmtPoster": "qien", "cmtC...   223.140.62.26   
7082  [{"cmtStatus": "推", "cmtPoster": "isaki1987", ...  114.26.205.222   
6130  [{"cmtStatus": "推", "cmtPoster": "isaki1987", ...  184.153.120.32   

             insertedDate dataSource  \
4347  2023-06-19 02:07:30        ptt   
6044  2023-12-15 02:19:21        ptt   
1658  2022-09-16 02:00:40        ptt   
7082  2024-03-16 02:24:04        ptt   
6130  2023-12-24 02:12:25        ptt   

                                              artComter  \
4347                [qaz996659, timer000, superfreeman]   
6044  [timer000, timer000, timer000, timer000, timer...   
1658  [qien, qien, miminiania, Suzy224, Suzy224, bal...   
7082                                [isaki1987, kazusn]   
6130  [isaki1987, tmac012004, qaz996659, qien, isaki...   

                              artStatus  
4347                          [→, 推, →]  
6044  [推, →, →, →, →, 推, →, 推, →, 推, →]  
1658                 [推, →, 推, 推, →, 推]  
7082                             [推, →]  
6130     [推, 推, →, 推, 推, 推, 推, →, 推, 推]

In [7]:
raw_data = raw_data.explode(['artComter','artStatus'])
socail_data = raw_data[['artUrl','artPoster','artComter','artStatus']]
socail_data.head(10)

artUrl     artPoster  \
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   

         artComter artStatus  
4347     qaz996659         →  
4347      timer000         推  
4347  superfreeman         →  
6044      timer000         推  
6044      timer000         →  
6044      timer000         →  
6044      timer000         →  
6044      timer000         →  
6044      addrying         推  
6044      addrying         →

In [8]:
socail_data.artStatus.unique()
# 可以看出憂鬱版是一個和諧的版面，彼此是互相支持的，沒有'噓'的行為發生

array(['→', '推'], dtype=object)

建立邊的資料

In [9]:
import random

# 發文者對文章
po_df = socail_data[['artPoster','artUrl']].drop_duplicates().rename(columns = {'artPoster':'src','artUrl':'dis'})

# sample 300 篇文章
random.seed(2024)
sample_url = random.choices(po_df.dis.unique().tolist(),k=300)
po_df = po_df[po_df.dis.isin(sample_url)]

# 留言者對文章，狀態為 weight
re_df = socail_data[['artComter','artUrl','artStatus']].rename(columns = {'artComter':'src','artUrl':'dis','artStatus':'weight'})
re_df = re_df[re_df.dis.isin(sample_url)]
re_df = re_df[~re_df['src'].isna()]
re_df.head()

src                                                dis weight
4347     qaz996659  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...      →
4347      timer000  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...      推
4347  superfreeman  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...      →
7170   bnbexp23ef1  https://www.ptt.cc/bbs/prozac/M.1711170631.A.2...      推
7170   bnbexp23ef1  https://www.ptt.cc/bbs/prozac/M.1711170631.A.2...      →

計算某留言者對文章的總評論分數
- 轉換邊的狀態 -> weight

In [10]:
def convertStatus(s):
  if s == '推':
    return 2
  elif s == '→':
    return 1
  else :
    return -1
re_df['weight'] = re_df['weight'].map(convertStatus)
# 計算某位留言者對某篇文章的總分數
re_df = re_df.groupby(['src','dis']).sum().reset_index()
re_df

src                                                dis  weight
0    Austin1102  https://www.ptt.cc/bbs/prozac/M.1696330052.A.4...       3
1    Austin1102  https://www.ptt.cc/bbs/prozac/M.1706617839.A.8...       6
2    Austin1102  https://www.ptt.cc/bbs/prozac/M.1707859018.A.C...       2
3       BeMessi  https://www.ptt.cc/bbs/prozac/M.1710000651.A.A...       3
4      Belieeve  https://www.ptt.cc/bbs/prozac/M.1658462639.A.8...       2
..          ...                                                ...     ...
793    yukilala  https://www.ptt.cc/bbs/prozac/M.1707859018.A.C...       2
794    yukilala  https://www.ptt.cc/bbs/prozac/M.1708386993.A.9...       1
795    yukilala  https://www.ptt.cc/bbs/prozac/M.1711197152.A.C...       2
796      zz3000  https://www.ptt.cc/bbs/prozac/M.1672279945.A.9...       2
797      zz3000  https://www.ptt.cc/bbs/prozac/M.1676837816.A.B...       4

[798 rows x 3 columns]

In [11]:
# 設定分數低的為紅色
def getColor(w):
  if w>0:
    return 'green'
  else:
    return 'red'
re_df['color'] = re_df.weight.map(getColor)
re_df

src                                                dis  weight  \
0    Austin1102  https://www.ptt.cc/bbs/prozac/M.1696330052.A.4...       3   
1    Austin1102  https://www.ptt.cc/bbs/prozac/M.1706617839.A.8...       6   
2    Austin1102  https://www.ptt.cc/bbs/prozac/M.1707859018.A.C...       2   
3       BeMessi  https://www.ptt.cc/bbs/prozac/M.1710000651.A.A...       3   
4      Belieeve  https://www.ptt.cc/bbs/prozac/M.1658462639.A.8...       2   
..          ...                                                ...     ...   
793    yukilala  https://www.ptt.cc/bbs/prozac/M.1707859018.A.C...       2   
794    yukilala  https://www.ptt.cc/bbs/prozac/M.1708386993.A.9...       1   
795    yukilala  https://www.ptt.cc/bbs/prozac/M.1711197152.A.C...       2   
796      zz3000  https://www.ptt.cc/bbs/prozac/M.1672279945.A.9...       2   
797      zz3000  https://www.ptt.cc/bbs/prozac/M.1676837816.A.B...       4   

     color  
0    green  
1    green  
2    green  
3    green  
4    green  
..     ...  
793  green  
794  green  
795  green  
796  green  
797  green  

[798 rows x 4 columns]

製作網路圖

In [12]:
# 人為綠色節點
# po文為橘色節點

# 建立一個網路圖
netWork = pyvis.network.Network(notebook=True, cdn_resources='in_line',directed=True)
# 所有發文者＋留言者
person = list(set(po_df.src.unique().tolist()+re_df.src.unique().tolist()))
url = po_df.dis.unique().tolist()

# 加入節點（人）
netWork.add_nodes(
    nodes = person,
    value = [1 for i in range(len(person))],
    color = ['#66CDAA' for i in range(len(person))],
    title = person
)
# 加入節點（文章）
netWork.add_nodes(
    nodes = url,
    value = [2 for i in range(len(url))],
    color = ['#FFB366' for i in range(len(url))],
    title = url
)

# 加入邊（發文者 -> 文章）
for i in po_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color='grey')
# 加入邊（留言者 -> 文章），顏色為某發文者對該文章的總分（>0:綠; <=0:紅）
for i in re_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color=i[3])

# 設定layout，圖節點之間的斥力
netWork.repulsion()

# netWork.show("./basic_netWork.html")
netWork.save_graph("./basic_netWork.html")
IPython.display.HTML('basic_netWork.html')

可以看出用戶都主要圍繞在某些貼文做分享。

# 網友之間的關係

In [13]:
pos_cmt = socail_data.copy()
pos_cmt = pos_cmt[~pos_cmt.artComter.isna()]
pos_cmt.head(10)

artUrl     artPoster  \
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
4347  https://www.ptt.cc/bbs/prozac/M.1687085306.A.A...  superfreeman   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   
6044  https://www.ptt.cc/bbs/prozac/M.1702530335.A.8...    cien881021   

         artComter artStatus  
4347     qaz996659         →  
4347      timer000         推  
4347  superfreeman         →  
6044      timer000         推  
6044      timer000         →  
6044      timer000         →  
6044      timer000         →  
6044      timer000         →  
6044      addrying         推  
6044      addrying         →

In [14]:
pos_cmt['score'] = pos_cmt['artStatus'].apply(lambda r: convertStatus(r))

# 某留言者對某發文者的總分
pos_cmt = pos_cmt.groupby(['artComter','artPoster']).sum('score').reset_index()
pos_cmt = pos_cmt[pos_cmt.score>=0]
pos_cmt = pos_cmt[pos_cmt.artComter != pos_cmt.artPoster]
# pos_cmt.score = 1
pos_cmt

artComter     artPoster  score
0        AreLies  notfound0506      2
1        AreLies   whitepoodle      1
3     Austin1102     ProfessUX      8
4     Austin1102     badshrimp      2
5     Austin1102      gagagaga      2
...          ...           ...    ...
2046      zz3000  notfound0506      4
2047      zz3000      pillow01      2
2048      zz3000     qaz996659      2
2049      zz3000        ui5550      3
2050      zz3000         vagor      2

[1964 rows x 3 columns]

In [15]:
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score').fillna(0)
mat

artPoster   Abysslol  AreLies  Auld1228  Austin1102  Belieeve  Busufu  CSimon  \
artComter                                                                       
AreLies          0.0      0.0       0.0         0.0       0.0     0.0     0.0   
Austin1102       0.0      0.0       0.0         0.0       0.0     0.0     0.0   
BeMessi          0.0      0.0       0.0         0.0       0.0     0.0     0.0   
Belieeve         0.0      0.0       0.0         0.0       0.0     0.0     0.0   
CBosh            0.0      0.0       0.0         0.0       0.0     0.0     0.0   
...              ...      ...       ...         ...       ...     ...     ...   
yukilala         0.0      0.0       6.0         2.0       0.0     0.0     0.0   
yule1224         0.0      0.0       0.0         0.0       0.0     0.0     0.0   
zshyGREEN        0.0      0.0       0.0         0.0       0.0     0.0     0.0   
zsquarez         0.0      0.0       0.0         0.0       0.0     0.0     0.0   
zz3000           0.0      0.0       0.0         0.0       0.0     0.0     0.0   

artPoster   Cecilia0905  Curiousecret  DickGrayson  ...  yahyah  yaliieah  \
artComter                                           ...                     
AreLies             0.0           0.0          0.0  ...     0.0       0.0   
Austin1102          0.0           0.0          0.0  ...     0.0       0.0   
BeMessi             0.0           0.0          0.0  ...     0.0       0.0   
Belieeve            0.0           0.0          0.0  ...     0.0       0.0   
CBosh               0.0           0.0          0.0  ...     0.0       0.0   
...                 ...           ...          ...  ...     ...       ...   
yukilala            0.0           0.0          0.0  ...     0.0       0.0   
yule1224            0.0           0.0          0.0  ...     0.0       0.0   
zshyGREEN           0.0           0.0          0.0  ...     0.0       0.0   
zsquarez            0.0           0.0          0.0  ...     0.0       0.0   
zz3000              0.0           0.0          0.0  ...     0.0       0.0   

artPoster   yamap82101  yeeee898  yoshi9145  yuki1037  yukilala  yuri99  \
artComter                                                                 
AreLies            0.0       0.0        0.0       0.0       0.0     0.0   
Austin1102         0.0       0.0        0.0       0.0       2.0     0.0   
BeMessi            0.0       0.0        0.0       0.0       0.0     0.0   
Belieeve           0.0       0.0        0.0       0.0       0.0     0.0   
CBosh              0.0       0.0        0.0       0.0       0.0     0.0   
...                ...       ...        ...       ...       ...     ...   
yukilala           0.0       0.0        0.0       0.0       0.0     0.0   
yule1224           0.0       0.0        0.0       0.0       0.0     0.0   
zshyGREEN          0.0       0.0        0.0       0.0       0.0     0.0   
zsquarez           0.0       0.0        0.0       0.0       0.0     0.0   
zz3000             0.0       0.0        0.0       0.0       0.0     0.0   

artPoster   z881331  zhickun  
artComter                     
AreLies         0.0      0.0  
Austin1102      0.0      0.0  
BeMessi         0.0      0.0  
Belieeve        0.0      0.0  
CBosh           0.0      0.0  
...             ...      ...  
yukilala        0.0      0.0  
yule1224        0.0      0.0  
zshyGREEN       0.0      0.0  
zsquarez        0.0      0.0  
zz3000          0.0      0.0  

[353 rows x 237 columns]

- mat: 有方向性，A -> B 分數與 B -> A 分數不一定一樣。
- mat_s: 無方向性（互動總分），A -> B 分數 +  B -> A 分數

In [16]:
# 所有留言者與發文者
pers = np.unique(pos_cmt[['artComter', 'artPoster']])

# 建立評分矩陣（留言者對發文者分數）
# 取得所有人對於其他人的分數（有方向性）
# 矩陣中的值 mat[i][j] 代表使用者 pers[i]（留言者）對使用者 pers[j]（發文者）的評分，
    # 留言者和發文者之間的關係是有方向的（即，mat[i][j] 不一定等於 mat[j][i]）
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score' ).fillna(0)\
  .reindex(columns=pers, index=pers, fill_value=0).to_numpy()
print(mat.shape)

# 取得所有人與其他人互動分數總和（無方向，兩個方向分數相加）
# 矩陣中的每一對元素都對稱，即 mat_s[i][j] 等於 mat_s[j][i]
# 對稱矩陣中的值 mat_s[i][j] 表示使用者 pers[i] 與使用者 pers[j] 之間的互動總分。
    # 透過將 pers[i] 對 pers[j] 的評分和 pers[j] 對 pers[i] 的評分相加而得到的。
# np.tril(mat, -1): 生成一個下三角矩陣（包括主對角線下方的所有元素，但不包括主對角線上的元素）
# np.triu(mat, 1): 生成一個上三角矩陣（包括主對角線上方的所有元素，但不包括主對角線上的元素）
tri = (np.tril(mat,-1).T + np.triu(mat,1))
mat_s = tri+tri.T # 上三角和下三角都包括在內，但對角線是 0
mat_s


(475, 475)


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

matPresentGraph()：用來將矩陣轉換為視覺化的網絡圖
- 利用 pyvis 來繪製網絡圖，並設定節點和邊的顏色。

In [17]:
# 產生隨機的顏色，畫圖使用
def random_color():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(),r(),r())

def matPresentGraph(mat:np.array, node_id:list, node_type:list=None, node_value:list=None, directed=True, edge_color=None) -> pyvis.network.Network:
  # 有方向或無方向
  if directed != True:
    # 矩陣對稱
    if (mat == mat.transpose()).all():
      print('matrix is Symmetric')
    # 矩陣不對稱
    else:
      print('matrix is not Symmetric')

  # 設定節點的類別及顏色
  # 沒有分節點類別
  if node_type == None:
    c = random_color()
    node_colors = [c for i in range(len(node_id))]
    node_type = [" " for i in range(len(node_id))]
  # 有分節點類別
  else:
    node_color_map = {}
    for i in set(node_type):
      # 幫每個類別產生一個顏色
      while True:
        c = random_color()
        if c not in node_color_map.values():
          break
      node_color_map[i] = c
    node_colors = [node_color_map[i] for i in node_type]
  # print(node_colors)

  # 如果沒有給邊的顏色，隨機產生一個
  if edge_color == None:
    edge_color = random_color()

  # 如果沒有給 node 值，就都分配 1
  if node_value == None:
    node_value = [1 for i in range(len(node_id))]

  # 建立圖
  net = pyvis.network.Network(notebook=True, directed = directed, cdn_resources='in_line')

  titles_list = []
  for i ,j in zip(node_id,node_type):
    titles_list.append(str(i)+":"+str(j))

  net.add_nodes(
      nodes = node_id,
      value = node_value,
      label = node_id,
      title = titles_list,
      color = node_colors
  )

  for row in range(len(node_id)):
    for col in range(len(node_id)):
      if mat[row][col]>0.:
        net.add_edge(
            node_id[row],node_id[col],width = mat[row][col],color = edge_color,title = mat[row][col]
        )
  net.repulsion()
  return net


設定網友的節點類型（同時為發文、留言者 / 發文者 / 留言者）

In [18]:
# 定義發文者（po）、評論者(cmt)、兩者兼具(both)
node_type = []

cmt_list = pos_cmt['artComter'].unique().tolist()
po_list = pos_cmt['artPoster'].unique().tolist()
both_list = list(set(cmt_list) & set(po_list))
for p in pers:
  if p in both_list:
    node_type.append('both')

  elif p in cmt_list:
    node_type.append('cmt')

  elif p in po_list:
    node_type.append('po')


In [19]:
net = matPresentGraph(mat=mat, node_id=pers, node_type=node_type)
net.save_graph("./pers_netWork.html")
IPython.display.HTML('pers_netWork.html')

大部分的節點都圍繞在both附近。

# Measures on node
- 目的：找出影響力大的節點（人）
- 方法：
    1. Eigenvector
    2. PageRank
    3. Hitss Score
    4. betweenness centrality

## 計算 eigenvector centrality （無向圖）
- 概念：與你連接的人越重要，你也越重要(有影響力)
- 連到的節點重要性較高，也會貢獻較大的重要性

特徵向量中心性是一種衡量節點在網絡中重要性的方法，它基於連接節點的重要性計算每個節點的中心性值。經過歸一化處理後，這些中心性值可以更方便地進行比較和可視化。

In [20]:
# nx.Graph(mat_s): 將對稱矩陣 mat_s 轉換為 NetworkX 的無向圖對象
# nx.eigenvector_centrality: 計算圖中每個節點的特徵向量中心性
# max_iter=10000: 演算法的最大迭代次數，以確保演算法收斂。 特徵向量中心性的計算是一個迭代過程，可能需要多次迭代才能達到穩定狀態。
eigenvec = np.array(list(nx.eigenvector_centrality(nx.Graph(mat_s),max_iter = 10000).values()))

# 將特徵向量中心性值歸一化到 [0, 1] 範圍內
eigenvec = (eigenvec-np.min(eigenvec))/(np.max(eigenvec)-np.min(eigenvec))

In [21]:
q = np.quantile(eigenvec,[.2,.4,.6,.8])
q

array([0.01304264, 0.02508246, 0.05912364, 0.13857354])

In [22]:
node_value = []


for i in eigenvec:
  # 越重要分數越高
  if i > q[3]:
    node_value.append(25)
  elif i >q[2]:
    node_value.append(20)
  elif i>q[1]:
    node_value.append(15)
  elif i>q[0]:
    node_value.append(10)
  else:
    node_value.append(5)
net = matPresentGraph(mat = mat_s,node_id = pers,node_type = node_type,node_value = node_value,directed=False)
net.save_graph("./pers_eig_netWork.html")
IPython.display.HTML('pers_eig_netWork.html')

matrix is Symmetric


可以發現有評論的文章且同時有多人評論的用戶，重要程度愈高（節點越大）

## PageRank (有向圖)
- 在一個有向圖中，PageRank 值高的節點通常是那些被很多其他節點連結到的節點，或是被一些重要節點連結到的節點

In [23]:
# Digraph 設定有向圖
# nx.DiGraph(mat): 使用 NetworkX 的 DiGraph 類別將矩陣 mat 轉換為有向圖物件。
# nx.pagerank(): 計算圖中每個節點的 PageRank 值
pagerank = np.array(list(nx.pagerank(nx.DiGraph(mat)).values()))
# pagerank = (pagerank-np.min(pagerank))/(np.max(pagerank)-np.min(pagerank))
pagerank

array([0.00088563, 0.00081876, 0.00308197, 0.00666875, 0.00071494,
       0.0010156 , 0.00073281, 0.00071494, 0.00227439, 0.00081716,
       0.00071494, 0.00092813, 0.00071494, 0.00071494, 0.00075115,
       0.00071494, 0.00071494, 0.00071494, 0.00071494, 0.00071494,
       0.00071494, 0.00072772, 0.00071494, 0.00071494, 0.0007559 ,
       0.00071494, 0.00071494, 0.00080175, 0.00077907, 0.00071494,
       0.00071494, 0.00074966, 0.00071494, 0.00149307, 0.00071494,
       0.0018731 , 0.00095604, 0.00300899, 0.00071494, 0.00071494,
       0.00205785, 0.00096371, 0.00071494, 0.00071494, 0.00071494,
       0.00071494, 0.0019362 , 0.00132263, 0.00178508, 0.00071494,
       0.04945778, 0.00071494, 0.00071494, 0.00071494, 0.00071494,
       0.0110436 , 0.00236217, 0.00082981, 0.00177155, 0.00071494,
       0.00071494, 0.00071494, 0.00071494, 0.00071494, 0.00071494,
       0.00071494, 0.01538498, 0.0011978 , 0.00071494, 0.00071494,
       0.00409063, 0.00071494, 0.00071494, 0.00071494, 0.00086

In [24]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=(pagerank*1000).tolist())
net.save_graph("./pers_page_netWork.html")
IPython.display.HTML('pers_page_netWork.html')

可以看出indegree較多，重要程度愈高(而那些節點也通常是both)

## Hits score （有向圖）
- 網頁重要性指標
    - index page (索引網頁，可以連結到其他網頁)：Hub Score 越高代表連到的 content page 都是 high authority score
    - content page (內容網頁)：authority score 越高代表越多 high hub score 的 index page 指向他

In [25]:
# nx.hits 計算圖中每個節點的 Hub 和 Authority 值。 HITS 演算法將每個節點分為兩種角色：
    # Hub： 一個好的 Hub 節點連結到許多 Authority 節點。
    # Authority： 一個好的 Authority 節點被許多 Hub 節點連結到。

# out_：每個節點的 Hub 值。
# in_：每個節點的 Authority 值。

out_,in_ = nx.hits(nx.DiGraph(mat),max_iter=100)

In [26]:
out_ = np.array(list(out_.values()))
out_q = np.quantile(out_,[.2,.4,.6,.8])
out_q

array([-0.00000000e+00,  2.26569663e-05,  1.22730459e-04,  6.45971817e-04])

In [27]:
in_ = np.array(list(in_.values()))
in_q = np.quantile(in_,[.2,.4,.6,.8])
in_q

array([-6.23366811e-20,  5.51327403e-19,  9.16981800e-05,  1.49502180e-03])

In [28]:
node_value = []

# 根據 Hub 值設定節點大小
for i in out_:
  if i > out_q[3]:
    node_value.append(25)
  elif i >out_q[2]:
    node_value.append(20)
  elif i>out_q[1]:
    node_value.append(15)
  elif i>out_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.save_graph("./pers_out_netWork.html")
IPython.display.HTML('pers_out_netWork.html')

可以發現連結到越重要的發文者（許多人也同時對他評論），自己也越重要</br>
(cmt和both的節點相對大)

In [29]:
node_value = []

# 根據 Authority 值設定節點大小
for i in in_:
  if i > in_q[3]:
    node_value.append(25)
  elif i >in_q[2]:
    node_value.append(20)
  elif i>in_q[1]:
    node_value.append(15)
  elif i>in_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.save_graph("./pers_in_netWork.html")
IPython.display.HTML('pers_in_netWork.html')

可以發現 indegree 的多寡會決定其重要程度

## betweenness centrality
- 中介中心性: 成為任兩節點之間的最短路徑次數
- 概念：連結到越多社群網路的節點，重要性越高

<img src="https://dist.neo4j.com/wp-content/uploads/20190201101243/betweenness-centrality-visualization-7.jpg" width="35%">

In [30]:
bet = np.array(list(nx.betweenness_centrality(nx.Graph(mat_s)).values()))
bet = (bet-np.min(bet))/(np.max(bet)-np.min(bet))
bet_q = np.quantile(bet,[.2,.4,.6,.8])

In [31]:
node_value = []
for i in bet:
  if i > bet_q[3]:
    node_value.append(25)
  elif i > bet_q[2]:
    node_value.append(20)
  elif i>bet_q[1]:
    node_value.append(15)
  elif i>bet_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat_s,node_id = pers,node_type = node_type,node_value=node_value ,directed=False)
net.save_graph("./pers_bet_netWork.html")
IPython.display.HTML('pers_bet_netWork.html')

matrix is Symmetric


可以看到與多個社群相連的人，越重要(通常此用戶的身分是both和po)


# Measures on graph

Transitivity/Density/Distance/Diameter/Clustering

計算最大的subgraph 的 measure

In [32]:
# 計算max subgraph
G = nx.Graph(mat_s)
G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
sub_mat = nx.adjacency_matrix(G_max_sub).todense()
node_idx = list(G_max_sub.nodes)
sub_pers = pers[node_idx]


畫出最大subgraph

In [33]:
net = matPresentGraph(mat=sub_mat,node_id=sub_pers,directed=False)
net.save_graph("./max_sub.html")
IPython.display.HTML('max_sub.html')

matrix is Symmetric


計算 transitivity
- transitivity 是衡量一個圖 (graph) 中閉合三角形比例的指標。在社交網絡或其他連結圖中，它反映了節點之間形成緊密社群的程度。

In [34]:
nx.transitivity(nx.Graph(sub_mat))

0.2064360339049872

計算 density （實際 edge 數/最大 edge 數）

In [35]:
nx.density(nx.Graph(sub_mat))

0.016479197723268734

計算 distance（平均每兩個節點的 shortest path 長度）

In [36]:
nx.average_shortest_path_length(nx.Graph(sub_mat))

2.9790938248181775

計算diameter（最長 shortest path 長度）

In [37]:
nx.diameter(nx.Graph(sub_mat))

6

計算 clustering

In [38]:
nx.average_clustering(nx.Graph(sub_mat))

0.20258884851775696